# Examples from the discrete world

The purpose of this notebook is to test our general methodology in a very basic setting. In this sense, 
1. we will assume a model in a discrete setting (e.g., a basic binomial model); 
2. we will generate the needed data from that model and "assume" we don't know from which model this data comes from;
3. and try to solve the problem for this data.

## 1. Create the model

In [39]:
from robust_pricing.path_generators import BinomialTree, Uniform, Gaussian, GaussianMartingale, UniformMartingale
from helper import *

In [80]:
path_length=2

volatility = 0.2
granularity = 1000

up_factor = np.exp(volatility * np.sqrt(1 / granularity))
down_factor = 1 / up_factor



observed_times = [i * (granularity // path_length) for i in range(1, path_length + 1)]

model = BinomialTree(
    path_length=path_length,
    mean=100,
    up_factor=up_factor,
    down_factor=down_factor,
    granularity=granularity,
    observed_times=observed_times,
)

In [81]:
data = model(10000).numpy()

In [82]:
hist_2d(data, 0, 1)

## 2. Create the inputs

In [83]:
%reload_ext autoreload
%autoreload 2
from robust_pricing.deePricing import *

## 2.1 The option portfolios

Based on this model, we need to create the base set of options $\mathcal{B}_t$ from which our (optimization) model will try to learn the model (probability measure) from which they come. For this task, we use the fact that we can sample from this model to price them using Monte-Carlo.

In [103]:
strike_prices = list(range(70, 130, 1))
pricing_data = model(10000)

option_portfolios = []

for t in range(path_length):
    calls = []
    puts = []
    for k in strike_prices:
        c = Call(strike=k, price=0)
        c.price = float(torch.mean(c(pricing_data[:, t])))
        p = Put(strike=k, price=0)
        p.price = float(torch.mean(p(pricing_data[:, t])))
        calls.append(c)
        puts.append(p)

    option_portfolios.append(
        OneMaturityOptionPortfolio(calls=calls, puts=puts)
    )
option_portfolio = DiagonalOptionPortfolio(option_portfolios)

## 2.2 The exotic option

In this case we will use a Lookback and/or Asian options:

In [104]:
K = 100
def f(x):
    return torch.relu(torch.mean(x, 1) - K)

Since we know the "right" model, we can use it to price the option using Monte-Carlo.

In [105]:
torch.mean(f(pricing_data))

tensor(6.2172)

## 2.3 We need to choose a model $\theta$ to sample from

In [127]:
# gm = Uniform(path_length, mean=model.mean, variance=20 ** 2)
# gm = GaussianMartingale(path_length, mean=model.mean, variance=20 ** 2)
# gm = UniformMartingale(path_length, mean=model.mean, variance=40 ** 2)
gm = model

In [128]:
data = gm(10000)
hist_2d(data, 0, 1)

## 2.4 Create the hedging strategies

## 2.5 Optimize

In [129]:
from copy import deepcopy

number_of_observations=1000
gamma = 30
no_trading_strategy = True


option_portfolio.reset_weights(zeros=False)

h_sup = HedgingStrategy(
    option_portfolio=deepcopy(option_portfolio),
    target_function=f,
    super_hedge=True,
    trading_kwargs=dict(num_layers=8, width_layers=100),
    no_trading_strategy=no_trading_strategy
)
h_sub = HedgingStrategy(
    option_portfolio=deepcopy(option_portfolio),
    target_function=f,
    super_hedge=False,
    trading_kwargs=dict(num_layers=8, width_layers=100),
    no_trading_strategy=no_trading_strategy    
)


h_sup.penalization_function.gamma = gamma
h_sub.penalization_function.gamma = gamma


h_sup.reset_weights(zeros=True)
h_sup.optimize(
    generator=gm, 
    number_of_observations=number_of_observations, 
    number_of_episodes=None,
)

h_sub.reset_weights(zeros=True)
h_sub.optimize(
    generator=gm, 
    number_of_observations=number_of_observations, 
    number_of_episodes=None,
)

In [130]:
h_sup.visualize_training_status()

In [131]:
h_sub.visualize_training_status()

## 2.6 "Validate"

Since in this example, we have the actual model from which the option prices come from, we can estimate the replication error against that model.

In [132]:
print(h_sup.replication_error(model(1000)))
print(h_sub.replication_error(model(1000)))

tensor(0.3284, grad_fn=<MeanBackward0>)
tensor(0.3770, grad_fn=<MeanBackward0>)


We can print the upper and lower bound for the option price given the observed prices:

In [133]:
print(f'Upper bound: {h_sup.value}')
print(f'Actual bound: {torch.mean(f(pricing_data))}')
print(f'Lower bound: {h_sub.value}')

Upper bound: 6.618958473205566
Actual bound: 6.217204570770264
Lower bound: 3.4761548042297363


## 3. Let's evaluate the impact of $\gamma$

Recall that the objective function we are minimizing penalizes the sup/sub-hedging constraint with a penalization function $\beta:\mathbb{R}\to\mathbb{R}_+$. In this example we are using 

$$ \beta(x) = \frac{1}{p}(\max\{x, 0 \})^p,$$
with $p=2$. For any penalization function $\beta$, we define and we define $\beta_\gamma:\mathbb{R}\to\mathbb{R}_+$

$$\beta_\gamma(x)=\frac{1}{\gamma}\beta(\gamma x).$$

In [39]:
low=1 
high=41
step=1 

lower_bound, upper_bound, sup_replication_error, sub_replication_error = run_for_gammas_in(
    generator=model, 
    test_data=model(1000),
    option_portfolio=option_portfolio,
    target_function=f,
    low=low, 
    high=high,
    step=step, 
    number_of_observations=500, 
    number_of_episodes=2500,
    no_trading_strategy=False,
    zeros=True
) 

(4.136599540710449, 2.1565732955932617)
(0.6821258664131165, 0.5961519479751587)
(3.6098616123199463, 2.7802977561950684)
(0.6015986800193787, 0.27454376220703125)
(3.3858048915863037, 2.9330081939697266)
(0.6291266083717346, 0.23405824601650238)
(3.140218734741211, 3.057051181793213)
(0.5410436987876892, 0.1569509208202362)
(3.021294593811035, 3.1131742000579834)
(0.5428246259689331, 0.14018072187900543)
(2.8497190475463867, 3.154036045074463)
(0.4704962372779846, 0.11211717128753662)
(2.8900787830352783, 3.1754658222198486)
(0.599380612373352, 0.1018448919057846)
(2.7292699813842773, 3.1979820728302)
(0.4850032925605774, 0.08806668967008591)
(2.648817539215088, 3.228407859802246)
(0.454651802778244, 0.07222321629524231)
(2.6360557079315186, 3.2387561798095703)
(0.5045550465583801, 0.06651517003774643)
(2.604045867919922, 3.2865068912506104)
(0.4961288571357727, 0.0703696683049202)
(2.5993127822875977, 3.2546145915985107)
(0.5305529832839966, 0.06699184328317642)
(2.519989490509033, 3

In [ ]:
plot_beta(2, max_gamma=4)

In [41]:
import plotly.graph_objects as go
# Create traces
fig = go.Figure()
x = list(range(low, high, step)) 

fig.add_trace(go.Scatter(
    x=x,
    y=sub_replication_error,
    mode='lines',
    name='sub_replication_error')
)

fig.add_trace(go.Scatter(
    x=x,
    y=sup_replication_error,
    mode='lines',
    name='sup_replication_error')
)

fig.update_layout(
    title="",
    xaxis_title=r"$\gamma$",
    yaxis_title=f"Replication error",
    legend_title="Bounds",

)

fig.show()

In [42]:
# Create traces
fig = go.Figure()
x = list(range(low, high, step))  

fig.add_trace(go.Scatter(
    x=x,
    y=lower_bound,
    mode='lines',
    name='lower_bound')
)

fig.add_trace(go.Scatter(
    x=x,
    y=upper_bound,
    mode='lines',
    name='upper_bound')
)

fig.update_layout(
    title="",
    xaxis_title=r"$\gamma$",
    yaxis_title=f"Solution",
    legend_title="Bounds",

)

fig.show()


## References
[1] Guo, G., & Obłój, J. (2019). Computational methods for martingale optimal transport problems. Annals of Applied Probability, 29(6), 3311–3347. https://doi.org/10.1214/19-AAP1481